In [1]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Wed Jun  3 12:57:49 2020

@author: josephharvey
"""
from datetime import datetime
from lorenzrungekutta_numba import rungekutta
# from lorenzrungekutta_numba import fx
# from lorenzrungekutta_numba import fy
# from lorenzrungekutta_numba import fz
import numpy as np
#from sklearn.linear_model import Ridge
from scipy import sparse
from scipy.linalg import solve
from scipy.optimize import minimize
from scipy.sparse.linalg import eigs
from scipy.stats import wasserstein_distance
from matplotlib import pyplot as plt

class Reservoir:
    def __init__(self, rk, rsvr_size = 300, spectral_radius = 0.6, input_weight = 1):
        self.rsvr_size = rsvr_size
        
        #get spectral radius < 1
        #gets row density = 0.03333
        unnormalized_W = (np.random.rand(rsvr_size,rsvr_size)*2 - 1)
        for i in range(unnormalized_W[:,0].size):
            for j in range(unnormalized_W[0].size):
                if np.random.rand(1) > 10/rsvr_size:
                    unnormalized_W[i][j] = 0
    
        max_eig = eigs(unnormalized_W, k = 1, return_eigenvectors = False, maxiter = 10**5)
        
        self.W = sparse.csr_matrix(spectral_radius/np.abs(max_eig)*unnormalized_W)
        
        const_conn = int(rsvr_size*0.15)
        Win = np.zeros((rsvr_size, 4))
        Win[:const_conn, 0] = (np.random.rand(Win[:const_conn, 0].size)*2 - 1)*input_weight
        Win[const_conn: const_conn + int((rsvr_size-const_conn)/3), 1] = (np.random.rand(Win[const_conn: const_conn + int((rsvr_size-const_conn)/3), 1].size)*2 - 1)*input_weight
        Win[const_conn + int((rsvr_size-const_conn)/3):const_conn + 2*int((rsvr_size-const_conn)/3), 2] = (np.random.rand(Win[const_conn + int((rsvr_size-const_conn)/3):const_conn + 2*int((rsvr_size-const_conn)/3), 2].size)*2 - 1)*input_weight
        Win[const_conn + 2*int((rsvr_size-const_conn)/3):, 3] = (np.random.rand(Win[const_conn + 2*int((rsvr_size-const_conn)/3):, 3].size)*2 - 1)*input_weight
        
        self.Win = sparse.csr_matrix(Win)
        self.X = (np.random.rand(rsvr_size, rk.train_length+2)*2 - 1)
        self.Wout = np.array([])

        self.data_trstates = 0
        self.states_trstates = 0
        
class RungeKutta:
    def __init__(self, x0 = 2,y0 = 2,z0 = 23, h = 0.01, T = 300, ttsplit = 5000, noise_scaling = 0):
        u_arr = rungekutta(x0,y0,z0,h,T)[:, ::10] 
        self.train_length = ttsplit
        
        u_arr[0] = (u_arr[0] - 0)/7.929788629895004
        u_arr[1] = (u_arr[1] - 0)/8.9932616136662
        u_arr[2] = (u_arr[2] - 23.596294463016896)/8.575917849311919
        
        self.u_arr_train = u_arr[:, :ttsplit+1] 
        #size 5001
        
        #noisy training array
        #switch to gaussian 
        noise = np.random.randn(self.u_arr_train[:,0].size, self.u_arr_train[0,:].size)*noise_scaling 
        self.u_arr_train_noise = self.u_arr_train + noise
        
        #plt.plot(self.u_arr_train_noise[0, :500])
        
        #u[5000], the 5001st element, is the last in u_arr_train and the first in u_arr_test
        self.u_arr_test = u_arr[:, ttsplit:]
        #size 1001
    
#takes a reservoir object res along with initial conditions
def getX(res, rk,x0 = 1,y0 = 1,z0 = 1, noise = False):
    
    if noise:
        u_training = rk.u_arr_train_noise
    else:
        u_training = rk.u_arr_train
    
    #loops through every timestep
    for i in range(0, u_training[0].size):
        u = np.append(1, u_training[:,i]).reshape(4,1)
        
        x = res.X[:,i].reshape(res.rsvr_size,1)
        x_update = np.tanh(np.add(res.Win.dot(u), res.W.dot(x)))
        
        res.X[:,i+1] = x_update.reshape(1,res.rsvr_size)    
    
    return res.X

def get_states(res, rk, skip = 150):
    Y_train = rk.u_arr_train_noise[:, skip+1:]
    X = getX(res, rk, noise = True)[:, skip+1:(res.X[0].size - 1)]
    X_train = np.concatenate((np.ones((1, rk.u_arr_train[0].size-(skip+1))), X, rk.u_arr_train_noise[:, skip:-1]), axis = 0)
    res.data_trstates = np.matmul(Y_train, np.transpose(X_train))
    res.states_trstates = np.matmul(X_train,np.transpose(X_train))

    return 
    
def trainRRM(res, rk, skip = 150, alpha = 10**-4):
    print("Training... ")

    alph = alpha
    #rrm = Ridge(alpha = alph, solver = 'cholesky')
    
    Y_train = rk.u_arr_train_noise[:, skip+1:]

    
    X = getX(res, rk, noise = True)[:, skip+1:(res.X[0].size - 1)]
    X_train = np.concatenate((np.ones((1, rk.u_arr_train[0].size-(skip+1))), X, rk.u_arr_train_noise[:, skip:-1]), axis = 0) 
    #X_train = np.copy(X)
    
    idenmat = np.identity(res.rsvr_size+4)*alph
    data_trstates = np.matmul(Y_train, np.transpose(X_train))
    states_trstates = np.matmul(X_train,np.transpose(X_train))
    res.Wout = np.transpose(solve(np.transpose(states_trstates + idenmat),np.transpose(data_trstates)))
    
    #optimization function needs perc. of stable res. 
    #scipy.optimize.minimize
    #https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.minimize.html#scipy.optimize.minimize
    
    #function which takes log of alpha, give perc. of stable reservoirs

    #split up train function to find matrices first, second one which computed Wout
    #https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.fminbound.html 
    #allows to set range of alpha

    print("Training complete ")
    #Y_train = Y_train.transpose()
    #X_train = X.transpose()
    
    #tweak regression param? use 10^-4, 10^-6
    #test Ridge() in simpler context
    #rrm.fit(X_train,Y_train)
    #res.Wout = rrm.coef_
    return res.Wout

def repeatTraining(res, T = 300, ttsplit = int(300/0.1), repeat_times = 10, skip = 150, noise_scaling = 0.1):
    ic = np.random.rand(3)*2-1
    rk = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = T, ttsplit = ttsplit, noise_scaling = noise_scaling)
    
    print("Training... ")

    alph = 10**-6
    #rrm = Ridge(alpha = alph, solver = 'cholesky')
    
    #train on 10 small training sets with different noise - minimize error over all
    #save the state of the reservoir for noisy datasets
    #also try - train on signal^2 or other function (get more info than just 3 vars) - no noise
    
    Y_train = rk.u_arr_train[:, skip+1:] 
    oneTime = rk.u_arr_train[:, skip+1:]
    
    X = getX(res, rk, noise = True)[:, skip+1:-1]
    
    Y_inputs = rk.u_arr_train_noise[:, skip:(rk.u_arr_train_noise[0].size - 1)]
    for i in range(repeat_times-1):
        Y_train = np.concatenate((Y_train, oneTime), axis = 1)
        noise = np.random.randn(rk.u_arr_train[:,0].size, rk.u_arr_train[0,:].size)*noise_scaling
        rk.u_arr_train_noise = rk.u_arr_train + noise 
        X = np.concatenate((X, getX(res, rk, noise = True)[:, skip+1:-1]), axis = 1)
        Y_inputs = np.concatenate((Y_inputs, rk.u_arr_train_noise[:, skip:(rk.u_arr_train_noise[0].size - 1)]), axis = 1) 
        
    X_train = np.concatenate((np.ones((1, repeat_times*(rk.u_arr_train[0].size-(skip+1)))), X, Y_inputs), axis = 0) 
    #X_train = np.copy(X)
    
    idenmat = np.identity(res.rsvr_size+4)*alph
    data_trstates = np.matmul(Y_train, np.transpose(X_train))
    states_trstates = np.matmul(X_train,np.transpose(X_train))
    res.Wout = np.transpose(solve(np.transpose(states_trstates + idenmat),np.transpose(data_trstates)))
    
    print("Training complete ")
    #Y_train = Y_train.transpose()
    #X_train = X.transpose()
    
    #tweak regression param? use 10^-4, 10^-6
    #test Ridge() in simpler context
    #rrm.fit(X_train,Y_train)
    #res.Wout = rrm.coef_
    return res.Wout 

def repeatTrainingAvg(res, T = 100, ttsplit = 400, repeat_times = 10, noise_scaling = 0.01): 
    rk = RungeKutta(T = T,ttsplit = ttsplit) 
    Wout_final = np.zeros((3,res.rsvr_size+4))
    
    for i in range(repeat_times):
        noise = np.random.randn(rk.u_arr_train[:,0].size, rk.u_arr_train[0,:].size)*noise_scaling 
        rk.u_arr_train_noise = rk.u_arr_train + noise
        Wout_final = np.add(Wout_final, trainRRM(res, rk, skip = 100))
    
    res.Wout = Wout_final/repeat_times
    
#CONCATENATE ALL THE DATA BEFORE RUNNING REGRESSION
    
def predict(res, x0 = 0, y0 = 0, z0 = 0, steps = 1000):
    Y = np.empty((3, steps + 1))
    X = np.empty((res.rsvr_size, steps + 1))
    
    Y[:,0] = np.array([x0,y0,z0]).reshape(1,3) 
    X[:,0] = res.X[:,-2]

    
    for i in range(0, steps):
        y_in = np.append(1, Y[:,i]).reshape(4,1)
        x_prev = X[:,i].reshape(res.rsvr_size,1)
        
        x_current = np.tanh(np.add(res.Win.dot(y_in), res.W.dot(x_prev)))
        X[:,i+1] = x_current.reshape(1,res.rsvr_size)
        #X = np.concatenate((X, x_current), axis = 1)
        y_out = np.matmul(res.Wout, np.concatenate((np.array([[1]]), x_current, Y[:,i].reshape(3,1)), axis = 0))
        #y_out = np.matmul(res.Wout, x_current)
        Y[:,i+1] = y_out.reshape(1, 3)
        

    return Y

def test(res, num_tests = 10, rkTime = 1000, split = 3000, showMapError = True, showTrajectories = True, showHist = True):

    stable_count = 0
    valid_time = np.array([])
    max_sum_square = np.array([])
    mean_sum_square = np.array([]) 
    means = np.zeros(num_tests)
    variances = np.zeros(num_tests)
    
    for i in range(num_tests):
        
        vtchange = 0
        x2y2z2 = np.array([])
    
        ic = np.random.rand(3)*2-1
        rktest = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = rkTime, ttsplit = split)
        res.X = (np.zeros((res.rsvr_size, split+2))*2 - 1)
        
        #sets res.X
        getX(res, rktest)
        
        pred = predict(res, x0 = rktest.u_arr_test[0,0], y0 = rktest.u_arr_test[1,0], z0 = rktest.u_arr_test[2,0], steps = (int(rkTime/0.1)-split))
        lorenz_map_x = np.zeros(pred[0].size)
        lorenz_map_x[0] = pred[0][0]
        
        check_vt = True
        for j in range(0, pred[0].size):
            if (j > 0):
                vtchange = vtchange + (rktest.u_arr_test[0, j] - rktest.u_arr_test[0, j-1])**2 + (rktest.u_arr_test[1, j] - rktest.u_arr_test[1, j-1])**2 + (rktest.u_arr_test[2, j] - rktest.u_arr_test[2, j-1])**2
                
                rkmap = RungeKutta(pred[0][j-1]*7.929788629895004, pred[1][j-1]*8.9932616136662, pred[2][j-1]*8.575917849311919+23.596294463016896, h=0.01, T=0.1)
                lorenz_map_x[j] = rkmap.u_arr_train[0][1] 
                
                #EXAMINE!!!
                x2error = (pred[0][j]-rkmap.u_arr_train[0][1])**2
                y2error = (pred[1][j]-rkmap.u_arr_train[1][1])**2
                z2error = (pred[2][j]-rkmap.u_arr_train[2][1])**2
                
                x2y2z2 = np.append(x2y2z2, (x2error+y2error+z2error)) 
                
            if (np.abs(pred[0, j] - rktest.u_arr_test[0, j]) > 1.5) and check_vt:
                valid_time = np.append(valid_time, j)
                
                print("Test " + str(i) + " valid time: " + str(j))
                check_vt = False
        
        x2y2z2 = x2y2z2/1.45
        #print(vtchange/(pred[0].size-1)) 
        #print("Mean: " + str(np.mean(pred[0])))
        #print("Variance: " + str(np.var(pred[0])))
        
        if showHist:
            plt.figure() 
            plt.hist(pred[0], bins = 11, label = "Predictions", alpha = 0.75)
            plt.hist(rktest.u_arr_test[0], bins = 11, label = "Truth", alpha = 0.75)
            plt.legend(loc="upper right")
        
        if showMapError:
            #plt.figure()
            #plt.plot(vector_field, label = "Vector Field Stability Metric")
            #plt.legend(loc="upper right") 

            plt.figure() 
            plt.plot(x2y2z2, label = "x + y + z square error")
            plt.legend(loc="upper right")
            
        if showTrajectories:
            plt.figure() 
            #plt.plot(lorenz_map_x, label = "Map Trajectory", color = "green") 
            plt.plot(pred[0], label = "Predictions")
            plt.plot(rktest.u_arr_test[0], label = "Truth") 
            plt.legend(loc="upper right") 
        
        print("Variance of lorenz data x dim: " + str(np.var(rktest.u_arr_test[0])))
        print("Variance of predictions: " + str(np.var(pred[0]))) 
        print("Max of total square error: " + str(max(x2y2z2)))
        print("Mean of total error: " + str(np.mean(x2y2z2)))
        print("Wasserstein distance: " + str(wasserstein_distance(pred[0], rktest.u_arr_test[0])))
        print()
        
        max_sum_square = np.append(max_sum_square, max(x2y2z2))
        mean_sum_square = np.append(mean_sum_square, np.mean(x2y2z2)) 
        
        means[i] = np.mean(pred[0])
        variances[i] = np.var(pred[0])
        
        if np.mean(x2y2z2) < 0.01 and 0.98 < np.var(pred[0]) and np.var(pred[0]) < 1.01:
            stable_count += 1
            print("stable")
            print()
        else:
            print("unstable")
            print() 
        
    
    
    if showMapError or showTrajectories or showHist:
        plt.show()
    
    #print("Variance of total square error: " + str(np.var(x2y2z2)))

    print("Avg. max sum square: " + str(np.mean(max_sum_square)))
    print("Avg. mean sum square: " + str(np.mean(mean_sum_square))) 
    print("Avg. of x dim: " + str(np.mean(means)))
    print("Var. of x dim: " + str(np.mean(variances)))
    print()
    
    
    return stable_count/num_tests

def generate_res(num_res, rk, res_size):

    reservoirs = []

    while len(reservoirs) < num_res:
        try:
            reservoirs.append(Reservoir(rk, rsvr_size = res_size, spectral_radius = 0.5, input_weight = 1.0))
            get_states(reservoirs[-1], rk, skip = 150) 
        except:
            print("eigenvalue error occured.")
    return reservoirs

def optim_func(reservoirs, alpha):

    results = np.array([])

    for res in reservoirs: 
        try:
            idenmat = np.identity(res.rsvr_size+4)*alpha
            res.Wout = np.transpose(solve(np.transpose(res.states_trstates + idenmat),np.transpose(res.data_trstates))) 

            results = np.append(results, test(res, 1, rkTime = 400, split = 2000, showMapError = False, showTrajectories = False, showHist = False))
        except:
            print("eigenvalue error occured.")

    return -1*np.mean(results)

def trainAndTest(alph):

    results = np.array([])
    num_res = 10

    for i in range(num_res):
        try:
            ic = np.random.rand(3)*2-1
            rk = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = 500, ttsplit = int(500/0.1), noise_scaling = 0.01)
            res = Reservoir(rk, rsvr_size = 100, spectral_radius = 0.5, input_weight = 1.0)
            
            trainRRM(res, rk, skip = 150, alpha = alph)
            
            results = np.append(results, test(res, 1, rkTime = 400, split = 2000, showMapError = False, showTrajectories = False, showHist = False))
        except:
            print("eigenvalue error occured.")
    return -1*np.mean(results)



########################################
np.random.seed(0)

train_time = 400
res_size = 100
res_per_test = 50
noise_values = np.logspace(-3.666666666666, 0, num = 12, base = 10)
alpha_values = np.logspace(-8, -2, 13)
stable_frac  = np.zeros(noise_values.size)
stable_frac_alpha  = np.zeros(noise_values.size)


#rk = RungeKutta(x0 = 1, y0 = 1, z0 = 30, T = train_time, ttsplit = int(train_time/0.1), noise_scaling = 0.01)
#reservoirs = generate_res(res_per_test, rk, res_size = res_size)

for i, noise in enumerate(noise_values):
    ic = np.random.rand(3)*2-1
    rk = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = train_time, ttsplit = int(train_time/0.1), noise_scaling = noise)
    
    reservoirs = generate_res(res_per_test, rk, res_size = res_size)
    #for r in reservoirs:
        #r.data_trstates = 0
        #r.states_trstates = 0 
    #    get_states(r, rk, skip = 150)

    min_optim_func = lambda alpha: optim_func(reservoirs, alpha)
    func_vals = np.zeros(alpha_values.size)
    for j in range(alpha_values.size):
        func_vals[j] = min_optim_func(alpha_values[j])
    result_fun = np.min(func_vals)
    result_x   = alpha_values[np.argmin(func_vals)]
    stable_frac[i] = -result_fun    
    stable_frac_alpha[i] = result_x
    """
    f = open("noise varying data", "a")
    now = datetime.now()
    currenttime = now.strftime("%H:%M:%S")
    f.write(currenttime)
    f.write("\n")
    f.write("noise level: " + str(noise))
    f.write("\n")
    f.write("res size: " + str(res_size))
    f.write("\n")
    f.write("train time: " + str(train_time))
    f.write("\n")
    f.write("max fraction of stable reservoirs: " + str(-1*result_fun))
    f.write("\n")
    f.write("optimal alpha: " + str(result_x))
    f.write("\n")
    f.write("\n")
    f.close()
    """

np.savetxt('stable_frac_%dnodes_%dtrainiters.csv' %(res_size, train_time), stable_frac, delimiter = ',')
np.savetxt('stable_frac_alpha_%dnodes_%dtrainiters.csv' %(res_size, train_time), stable_frac_alpha, delimiter = ',')

Test 0 valid time: 26
Variance of lorenz data x dim: 0.9876993584432029
Variance of predictions: 0.9946282595608007
Max of total square error: 0.03320560785210374
Mean of total error: 0.0005906721743081897
Wasserstein distance: 0.12643828411245223

stable

Avg. max sum square: 0.03320560785210374
Avg. mean sum square: 0.0005906721743081897
Avg. of x dim: -0.01668431210008458
Var. of x dim: 0.9946282595608007

Test 0 valid time: 36
Variance of lorenz data x dim: 0.9953183317632648
Variance of predictions: 0.04330454357493715
Max of total square error: 0.010857645815397325
Mean of total error: 0.0002981144858563089
Wasserstein distance: 1.235959803139949

unstable

Avg. max sum square: 0.010857645815397325
Avg. mean sum square: 0.0002981144858563089
Avg. of x dim: 1.0506322475401462
Var. of x dim: 0.04330454357493715

Test 0 valid time: 81
Variance of lorenz data x dim: 0.9909682583630868
Variance of predictions: 0.9931559437770794
Max of total square error: 0.03112607390149595
Mean of t

c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:213: RuntimeWarning: overflow encountered in matmul
c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:213: RuntimeWarning: invalid value encountered in matmul
c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:250: RuntimeWarning: overflow encountered in double_scalars


Variance of lorenz data x dim: 0.9954333109344028
Variance of predictions: nan
Max of total square error: 28611.764978661242
Mean of total error: nan
Wasserstein distance: nan

unstable

Avg. max sum square: 28611.764978661242
Avg. mean sum square: nan
Avg. of x dim: nan
Var. of x dim: nan

Test 0 valid time: 31
Variance of lorenz data x dim: 0.9907191093544072
Variance of predictions: inf
Max of total square error: 19352.824260761223
Mean of total error: nan
Wasserstein distance: 1.4956245267180439e+186

unstable

Avg. max sum square: 19352.824260761223
Avg. mean sum square: nan
Avg. of x dim: 2.8017602097135305e+185
Var. of x dim: inf

Test 0 valid time: 51


c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\numpy\core\_methods.py:205: RuntimeWarning: overflow encountered in multiply
  x = um.multiply(x, x, out=x)


Variance of lorenz data x dim: 0.9956166102689011
Variance of predictions: 0.27660333304277174
Max of total square error: 21.988009832212597
Mean of total error: 1.9083374670175393
Wasserstein distance: 0.9985677181775924

unstable

Avg. max sum square: 21.988009832212597
Avg. mean sum square: 1.9083374670175393
Avg. of x dim: -0.8862114360058008
Var. of x dim: 0.27660333304277174

Test 0 valid time: 77
Variance of lorenz data x dim: 1.0012211642690383
Variance of predictions: 1.0028910499578452
Max of total square error: 0.03636871136662659
Mean of total error: 0.0008320701805763657
Wasserstein distance: 0.09967547123651503

stable

Avg. max sum square: 0.03636871136662659
Avg. mean sum square: 0.0008320701805763657
Avg. of x dim: -0.06477456090601197
Var. of x dim: 1.0028910499578452

Test 0 valid time: 33
Variance of lorenz data x dim: 0.9956041843868524
Variance of predictions: 87.7598776638612
Max of total square error: 3406.0244664762063
Mean of total error: 383.08968315636054
Wa

...

Variance of lorenz data x dim: 0.9887367814062819
Variance of predictions: 0.06511405750419336
Max of total square error: 0.6596688263295811
Mean of total error: 0.12881512734122866
Wasserstein distance: 1.1129977393629111

unstable

Avg. max sum square: 0.6596688263295811
Avg. mean sum square: 0.12881512734122866
Avg. of x dim: -0.9034940054400651
Var. of x dim: 0.06511405750419336

Test 0 valid time: 58
Variance of lorenz data x dim: 0.9975593219830006
Variance of predictions: 0.09144692775999236
Max of total square error: 0.6751797122388247
Mean of total error: 0.14576220631196027
Wasserstein distance: 0.9380969989317108

unstable

Avg. max sum square: 0.6751797122388247
Avg. mean sum square: 0.14576220631196027
Avg. of x dim: 0.8370905713707004
Var. of x dim: 0.09144692775999236

Test 0 valid time: 4
Variance of lorenz data x dim: 0.9967086638994486
Variance of predictions: 0.08038264151034208
Max of total square error: 0.4462455219584754
Mean of total error: 0.05590176749772548
Wa

Variance of lorenz data x dim: 0.9945043696969117
Variance of predictions: 0.0916358020189812
Max of total square error: 0.14741438933688275
Mean of total error: 0.03668974884132686
Wasserstein distance: 1.103774559233453

unstable

Avg. max sum square: 0.14741438933688275
Avg. mean sum square: 0.03668974884132686
Avg. of x dim: 0.9877574154295674
Var. of x dim: 0.0916358020189812

Test 0 valid time: 13
Variance of lorenz data x dim: 0.9931735299375198
Variance of predictions: 0.15259772501682495
Max of total square error: 0.26401279398211025
Mean of total error: 0.08480908556847445
Wasserstein distance: 0.9361251451229211

unstable

Avg. max sum square: 0.26401279398211025
Avg. mean sum square: 0.08480908556847445
Avg. of x dim: 0.8031501781784911
Var. of x dim: 0.15259772501682495

Test 0 valid time: 21
Variance of lorenz data x dim: 0.9945614978608729
Variance of predictions: 0.04869561815902596
Max of total square error: 0.269804016185459
Mean of total error: 0.0956715433190916
Was

Variance of lorenz data x dim: 0.9926794465713839
Variance of predictions: 0.08190897942389243
Max of total square error: 0.3801343987202829
Mean of total error: 0.13333056098253435
Wasserstein distance: 0.9131810520374511

unstable

Avg. max sum square: 0.3801343987202829
Avg. mean sum square: 0.13333056098253435
Avg. of x dim: 0.8959372807706767
Var. of x dim: 0.08190897942389243

Test 0 valid time: 6
Variance of lorenz data x dim: 0.9917317400090895
Variance of predictions: 0.08909694032573345
Max of total square error: 1.0614006080255933
Mean of total error: 0.24073400711192738
Wasserstein distance: 0.6628361891136196

unstable

Avg. max sum square: 1.0614006080255933
Avg. mean sum square: 0.24073400711192738
Avg. of x dim: 0.4962850010686612
Var. of x dim: 0.08909694032573345

Test 0 valid time: 14
Variance of lorenz data x dim: 0.9948524181617152
Variance of predictions: 0.0007935639194934293
Max of total square error: 0.18520748059633751
Mean of total error: 0.0239896733732383
W

Wasserstein distance: 1.1080543914808265

unstable

Avg. max sum square: 0.8005809940120442
Avg. mean sum square: 0.13261969638919185
Avg. of x dim: 0.9513317398360028
Var. of x dim: 0.07661630224758546

Test 0 valid time: 31
Variance of lorenz data x dim: 0.9994942920750102
Variance of predictions: 0.0714857597474941
Max of total square error: 0.13874134682063005
Mean of total error: 0.08043013215481364
Wasserstein distance: 1.0849787603700694

unstable

Avg. max sum square: 0.13874134682063005
Avg. mean sum square: 0.08043013215481364
Avg. of x dim: -0.9729380110272033
Var. of x dim: 0.0714857597474941

Test 0 valid time: 15
Variance of lorenz data x dim: 0.983519420547704
Variance of predictions: 0.09361738760761415
Max of total square error: 0.33193134665444796
Mean of total error: 0.13302273864316122
Wasserstein distance: 0.8858564453624269

unstable

Avg. max sum square: 0.33193134665444796
Avg. mean sum square: 0.13302273864316122
Avg. of x dim: -0.9704761239576877
Var. of x dim

Variance of lorenz data x dim: 0.9987583454287732
Variance of predictions: 0.08761812089929166
Max of total square error: 0.39956515862826736
Mean of total error: 0.10201961622452864
Wasserstein distance: 1.0122146959085956

unstable

Avg. max sum square: 0.39956515862826736
Avg. mean sum square: 0.10201961622452864
Avg. of x dim: -1.0048711533875745
Var. of x dim: 0.08761812089929166

Test 0 valid time: 12
Variance of lorenz data x dim: 0.9942888240220451
Variance of predictions: 0.12703526335880375
Max of total square error: 0.6491240487436591
Mean of total error: 0.23401149437797555
Wasserstein distance: 0.752298742093015

unstable

Avg. max sum square: 0.6491240487436591
Avg. mean sum square: 0.23401149437797555
Avg. of x dim: 0.6626857123974721
Var. of x dim: 0.12703526335880375

Test 0 valid time: 22
Variance of lorenz data x dim: 0.9966137738957287
Variance of predictions: 0.03264693237672419
Max of total square error: 0.18008810425638944
Mean of total error: 0.08481962472123039